# IBM DATA SCIENCE CAPSTONE

#WEEK 3 SEGMENTING AND CLUSTERING NEIGHBORHOODS IN TORONTO

In [3]:
import sys
!{sys.executable} -m pip install geocoder
!{sys.executable} -m pip install folium

print('Packages installed.')

Packages installed.


In [5]:
import numpy as np # library to handle data in a vectorized manner
import pandas as pd # library for data analsysis
import geocoder # import geocoder
import requests 
from bs4 import BeautifulSoup 

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.cluster import KMeans

#!conda install -c conda-forge folium=0.5.0 --yes # uncomment this line if you haven't completed the Foursquare API lab
import folium # map rendering library


print('Libraries imported.')

Libraries imported.


#RAW DATA

In [15]:
URL = "https://en.wikipedia.org/wiki/List_of_postal_codes_of_Canada:_M"
r = requests.get(URL).text

soup = BeautifulSoup(r)
table = soup.find('div', class_ = 'mw-parser-output') 
data_table = table.table.tbody

# print(soup.prettify()) 
print('Page Ok.')

Page Ok.


In [19]:
columns = ['PostalCode', 'Borough', 'Neighbourhood']
data = dict({key:[]*len(columns) for key in columns})

for row in data_table.find_all('tr'):
    for i,column in zip(row.find_all('td'),columns):
        i = i.text
        i = i.replace('\n', '')
        data[column].append(i)
        
df = pd.DataFrame.from_dict(data=data)[columns]
print(df.shape)
df.head()

(180, 3)


PostalCode           Borough              Neighbourhood
0        M1A      Not assigned               Not assigned
1        M2A      Not assigned               Not assigned
2        M3A        North York                  Parkwoods
3        M4A        North York           Victoria Village
4        M5A  Downtown Toronto  Regent Park, Harbourfront

In [23]:
df[:0]

Empty DataFrame
Columns: [PostalCode, Borough, Neighbourhood]
Index: []

In [25]:
df

PostalCode           Borough  \
0          M3A        North York   
1          M4A        North York   
2          M5A  Downtown Toronto   
3          M6A        North York   
4          M7A  Downtown Toronto   
..         ...               ...   
98         M8X         Etobicoke   
99         M4Y  Downtown Toronto   
100        M7Y      East Toronto   
101        M8Y         Etobicoke   
102        M8Z         Etobicoke   

                                         Neighbourhood  
0                                            Parkwoods  
1                                     Victoria Village  
2                            Regent Park, Harbourfront  
3                     Lawrence Manor, Lawrence Heights  
4          Queen's Park, Ontario Provincial Government  
..                                                 ...  
98       The Kingsway, Montgomery Road, Old Mill North  
99                                Church and Wellesley  
100  Business reply mail Processing Centre, South C...  
101  Old Mill South, King's Mill Park, Sunnylea, Hu...  
102  Mimico NW, The Queensway West, South of Bloor,...  

[103 rows x 3 columns]

In [26]:
p, b, n = [], [], []
for postcode, borough, neigh in zip(df['PostalCode'], df['Borough'], df['Neighbourhood']):
    p.append(postcode)
    b.append(borough)
    if neigh == 'Not assigned':
        n.append(borough)
    else:
        n.append(neigh)

df = pd.DataFrame({'PostalCode': p, 'Borough': b, 'Neighbourhood':n})[columns]
print(df.shape)
df.head()

(103, 3)


PostalCode           Borough                                Neighbourhood
0        M3A        North York                                    Parkwoods
1        M4A        North York                             Victoria Village
2        M5A  Downtown Toronto                    Regent Park, Harbourfront
3        M6A        North York             Lawrence Manor, Lawrence Heights
4        M7A  Downtown Toronto  Queen's Park, Ontario Provincial Government

In [34]:
df.head()

Postal Code           Borough                                Neighbourhood
0         M3A        North York                                    Parkwoods
1         M4A        North York                             Victoria Village
2         M5A  Downtown Toronto                    Regent Park, Harbourfront
3         M6A        North York             Lawrence Manor, Lawrence Heights
4         M7A  Downtown Toronto  Queen's Park, Ontario Provincial Government

#FINAL DATA

In [40]:
postcodes = df['Postal Code'].values
boroughs = df['Borough'].values
neighs = df['Neighbourhood'].values

#create a dictionary with keys as Postcode and Borough, keys of dictioaries are unique
dic = dict({(key1,key2): [] for key1, key2 in zip(postcodes, boroughs)})
print('Number of keys in the dictionary are: ', len(dic.keys()))

#filling the values of keys of dictionary
for postcode, borough, neigh in zip(postcodes,boroughs, neighs):
    key = (postcode, borough)
    dic[key].append(neigh)

df = pd.DataFrame(columns = ['Postal Code', 'Borough', 'Neighbourhood'])
for key, value in dic.items():
    postcode, borough, neig = key[0], key[1], value
    neig = ', '.join(neig)
    df = df.append({'Postal Code': postcode,
                     'Borough': borough,
                     'Neighbourhood': neig}, ignore_index = True)
print('Total Final data is: ', df.shape)
df.head(10)

Number of keys in the dictionary are:  103
Total Final data is:  (103, 3)


Postal Code           Borough                                Neighbourhood
0         M3A        North York                                    Parkwoods
1         M4A        North York                             Victoria Village
2         M5A  Downtown Toronto                    Regent Park, Harbourfront
3         M6A        North York             Lawrence Manor, Lawrence Heights
4         M7A  Downtown Toronto  Queen's Park, Ontario Provincial Government
5         M9A         Etobicoke      Islington Avenue, Humber Valley Village
6         M1B       Scarborough                               Malvern, Rouge
7         M3B        North York                                    Don Mills
8         M4B         East York              Parkview Hill, Woodbine Gardens
9         M5B  Downtown Toronto                     Garden District, Ryerson

In [41]:
df.shape

(103, 3)

In [62]:
df_geo = pd.read_csv('Geospatial_Coordinates.csv')
df_geo

Postal Code   Latitude  Longitude
0           M1B  43.806686 -79.194353
1           M1C  43.784535 -79.160497
2           M1E  43.763573 -79.188711
3           M1G  43.770992 -79.216917
4           M1H  43.773136 -79.239476
..          ...        ...        ...
98          M9N  43.706876 -79.518188
99          M9P  43.696319 -79.532242
100         M9R  43.688905 -79.554724
101         M9V  43.739416 -79.588437
102         M9W  43.706748 -79.594054

[103 rows x 3 columns]

In [74]:
df_geo = pd.read_csv('Geospatial_Coordinates.csv')
df_geo = pd.merge(df, df_geo, how='inner', on='Postal Code')

    
print(df_geo.shape)
df_geo.head(10)

(103, 5)


Postal Code           Borough                                Neighbourhood  \
0         M3A        North York                                    Parkwoods   
1         M4A        North York                             Victoria Village   
2         M5A  Downtown Toronto                    Regent Park, Harbourfront   
3         M6A        North York             Lawrence Manor, Lawrence Heights   
4         M7A  Downtown Toronto  Queen's Park, Ontario Provincial Government   
5         M9A         Etobicoke      Islington Avenue, Humber Valley Village   
6         M1B       Scarborough                               Malvern, Rouge   
7         M3B        North York                                    Don Mills   
8         M4B         East York              Parkview Hill, Woodbine Gardens   
9         M5B  Downtown Toronto                     Garden District, Ryerson   

    Latitude  Longitude  
0  43.753259 -79.329656  
1  43.725882 -79.315572  
2  43.654260 -79.360636  
3  43.718518 -79.464763  
4  43.662301 -79.389494  
5  43.667856 -79.532242  
6  43.806686 -79.194353  
7  43.745906 -79.352188  
8  43.706397 -79.309937  
9  43.657162 -79.378937

In [83]:
import numpy as np # library to handle data in a vectorized manner

import pandas as pd # library for data analsysis
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

import json # library to handle JSON files

!conda install -c conda-forge geopy --yes

import requests # library to handle requests
from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.cluster import KMeans

!conda install -c conda-forge folium=0.5.0 --yes
import folium # map rendering library

print('Libraries imported.')

Solving environment: ...working... done

# All requested packages already installed.

Solving environment: ...working... done

# All requested packages already installed.

Libraries imported.


In [84]:
from geopy.geocoders import Nominatim

In [108]:
with open('Neighbourhood Crime Rates.geojson') as json_data:
    df_geo2 = json.load(json_data)

In [109]:
df_geo2

{'type': 'FeatureCollection',
 'crs': {'type': 'name',
  'properties': {'name': 'urn:ogc:def:crs:OGC:1.3:CRS84'}},
 'features': [{'type': 'Feature',
   'properties': {'_id': 1,
    'OBJECTID': 16,
    'Neighbourhood': 'South Parkdale',
    'Hood_ID': 85,
    'Population': 21849,
    'Assault_2014': 202,
    'Assault_2015': 226,
    'Assault_2016': 231,
    'Assault_2017': 229,
    'Assault_2018': 220,
    'Assault_2019': 251,
    'Assault_AVG': 226.5,
    'Assault_CHG': 0.14,
    'Assault_Rate_2019': 1148.8,
    'AutoTheft_2014': 13,
    'AutoTheft_2015': 20,
    'AutoTheft_2016': 23,
    'AutoTheft_2017': 19,
    'AutoTheft_2018': 17,
    'AutoTheft_2019': 20,
    'AutoTheft_AVG': 18.7,
    'AutoTheft_CHG': 0.18,
    'AutoTheft_Rate_2019': 91.5,
    'BreakandEnter_2014': 45,
    'BreakandEnter_2015': 51,
    'BreakandEnter_2016': 71,
    'BreakandEnter_2017': 58,
    'BreakandEnter_2018': 78,
    'BreakandEnter_2019': 89,
    'BreakandEnter_AVG': 65.3,
    'BreakandEnter_CHG': 0.14,
 

In [110]:
neighborhoods_data = df_geo2['features']

In [112]:
neighborhoods_data[0]

{'type': 'Feature',
 'properties': {'_id': 1,
  'OBJECTID': 16,
  'Neighbourhood': 'South Parkdale',
  'Hood_ID': 85,
  'Population': 21849,
  'Assault_2014': 202,
  'Assault_2015': 226,
  'Assault_2016': 231,
  'Assault_2017': 229,
  'Assault_2018': 220,
  'Assault_2019': 251,
  'Assault_AVG': 226.5,
  'Assault_CHG': 0.14,
  'Assault_Rate_2019': 1148.8,
  'AutoTheft_2014': 13,
  'AutoTheft_2015': 20,
  'AutoTheft_2016': 23,
  'AutoTheft_2017': 19,
  'AutoTheft_2018': 17,
  'AutoTheft_2019': 20,
  'AutoTheft_AVG': 18.7,
  'AutoTheft_CHG': 0.18,
  'AutoTheft_Rate_2019': 91.5,
  'BreakandEnter_2014': 45,
  'BreakandEnter_2015': 51,
  'BreakandEnter_2016': 71,
  'BreakandEnter_2017': 58,
  'BreakandEnter_2018': 78,
  'BreakandEnter_2019': 89,
  'BreakandEnter_AVG': 65.3,
  'BreakandEnter_CHG': 0.14,
  'BreakandEnter_Rate_2019': 407.3,
  'Homicide_2014': 0,
  'Homicide_2015': 0,
  'Homicide_2016': 1,
  'Homicide_2017': 0,
  'Homicide_2018': 0,
  'Homicide_2019': 1,
  'Homicide_AVG': 0.3,
 

In [113]:
# define the dataframe columns
column_names = ['Borough', 'Neighborhood', 'Latitude', 'Longitude'] 

# instantiate the dataframe
neighborhoods = pd.DataFrame(columns=column_names)

In [114]:
neighborhoods

Empty DataFrame
Columns: [Borough, Neighborhood, Latitude, Longitude]
Index: []

In [130]:
for data in neighborhoods_data:
    borough = neighborhood_name = data['properties']['Population'] 
    neighborhood_name = data['properties']['Hood_ID']
    
    neighborhood_latlon = data['geometry']['coordinates']
    neighborhood_lat = neighborhood_latlon[0]
    neighborhood_lon = neighborhood_latlon[0]
    
    neighborhoods = neighborhoods.append({'Borough': borough,
                                          'Neighborhood': neighborhood_name,
                                          'Latitude': neighborhood_lat,
                                          'Longitude': neighborhood_lon}, ignore_index=True)

In [131]:
neighborhoods.head()

Borough Neighborhood                                           Latitude  \
0   21849           85  [[-79.4277365687988, 43.6297930851501], [-79.4...   
1   27876           70  [[-79.3286449860498, 43.6474512417408], [-79.3...   
2   17812           40  [[-79.3438610732307, 43.7564969057502], [-79.3...   
3   15683           61  [[-79.28771591526392, 43.6897779527472], [-79....   
4   12416           21  [[-79.5806033091641, 43.7630193015899], [-79.5...   

                                           Longitude  
0  [[-79.4277365687988, 43.6297930851501], [-79.4...  
1  [[-79.3286449860498, 43.6474512417408], [-79.3...  
2  [[-79.3438610732307, 43.7564969057502], [-79.3...  
3  [[-79.28771591526392, 43.6897779527472], [-79....  
4  [[-79.5806033091641, 43.7630193015899], [-79.5...

In [132]:
print('The dataframe has {} boroughs and {} neighborhoods.'.format(
        len(neighborhoods['Borough'].unique()),
        neighborhoods.shape[0]
    )
)

The dataframe has 140 boroughs and 140 neighborhoods.


In [133]:
address = 'Toronto'

geolocator = Nominatim(user_agent="ny_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of Toronto are {}, {}.'.format(latitude, longitude))

The geograpical coordinate of Toronto are 43.6534817, -79.3839347.


In [137]:
# create map of Toronto using latitude and longitude values
map_toronto = folium.Map(location=[latitude, longitude], zoom_start=10)

# add markers to map
for lat, lng, borough, neighborhood in zip(neighborhoods['Latitude'], neighborhoods['Longitude'], neighborhoods['Borough'], neighborhoods['Neighborhood']):
    label = '{}, {}'.format(neighborhood, borough)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_toronto)  
    
map_toronto

#FINISH